In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import os
import sys
import bs4 


import tensorflow as tf


from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.layers import Embedding,GRU,Dense,Conv2D,MaxPool2D,Input,Dropout,Activation,Bidirectional,Concatenate,Lambda,Reshape,Conv1D,MaxPooling1D
from tensorflow.keras.utils import to_categorical
import tensorflow.keras.backend as K
import numpy as np


In [ ]:
disease_f = os.listdir('/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation')
tourism_f = os.listdir('/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/news_articles_and_heritage/Training')
tourism_f_test = os.listdir('/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/news_articles_and_heritage/Testing')

In [ ]:
disease_f_1 = os.listdir('/content/drive/My Drive/DATA SETS/Hindi-domain-treebank/Hindi-Diseases/Data')
tourism_f_1 = os.listdir('/content/drive/My Drive/DATA SETS/Hindi-domain-treebank/Hindi-Tourism/Data')

In [ ]:
!pip install tensorflow==1.15.0

In [ ]:
disease_ff_1 = ["/content/drive/My Drive/DATA SETS/Hindi-domain-treebank/Hindi-Diseases/Data/" + x for x in disease_f_1]
tourism_ff_1 = ["/content/drive/My Drive/DATA SETS/Hindi-domain-treebank/Hindi-Tourism/Data/" + x for x in tourism_f_1]

In [ ]:
disease_ff = ["/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/" + x for x in disease_f]
tourism_ff = ["/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/news_articles_and_heritage/Training/" + x for x in tourism_f]
tourism_ff_test = ["/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/news_articles_and_heritage/Testing/" + x for x in tourism_f_test]


In [ ]:
print(disease_ff)
print(tourism_ff)
tourism_ff = tourism_ff+tourism_ff_test
print(len(tourism_ff))

['/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/file-khadi_ka_kurtha-0807112238.dat', '/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/file-andhe_ki_lathi-1507111038.dat~', '/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/file-sapna-0707111503.dat', '/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/file-yes-sir-0707111505.dat', '/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/file-udhaar-0707111504.dat', '/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/file-rishthey_ka_dhaag-0807112232.dat', '/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/file-andhe_ki_lathi-1507111038.dat', '/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/conversation/file-mouth_ka_saudagar-1507111034.dat', '/content/drive/My Drive/Domain_Hindi/HDTB_pre_release_version-0.05/con

In [ ]:
def part_preprocess(fileName,dis_feature_data,dis_label_data):
  f = open(fileName,'r').read()
  soup = bs4.BeautifulSoup(f)
  all_sentence = soup.find_all('sentence')
  for j in range(len(all_sentence)):
    sing = all_sentence[j]
    feature_post_elem = []
    label_post_elem = []
    z = (sing.get_text()).replace("\t"," ").split("))")
    for i in range(len(z)):
      part_sent = (z[i].split("\n"))
      for x in part_sent:
        if(x!="" and x!=" "):
          a = x.split(" ")
          if(a[2]!=""):
            feature_post_elem.append(a[1])
            label_post_elem.append(a[2])
            
    dis_feature_data.append(feature_post_elem)
    dis_label_data.append(label_post_elem)



In [ ]:

dis_feature_data = []
dis_label_data = []
for i in range(len(disease_ff)):
  part_preprocess(disease_ff[i],dis_feature_data,dis_label_data)

In [ ]:
k=[]
for i in dis_label_data:
  k.append((len(i)))
print(len(dis_label_data))
print(len(tourism_ff))
print(k)

2196
1063
[18, 21, 21, 13, 20, 8, 14, 17, 20, 12, 23, 16, 13, 7, 20, 30, 28, 25, 16, 21, 37, 24, 18, 25, 15, 22, 27, 16, 16, 11, 14, 27, 21, 29, 24, 32, 32, 24, 16, 20, 36, 43, 16, 24, 16, 8, 11, 38, 22, 24, 15, 21, 19, 16, 29, 20, 34, 19, 23, 13, 24, 21, 15, 19, 52, 12, 28, 52, 47, 16, 17, 17, 24, 28, 23, 22, 32, 15, 29, 8, 19, 16, 30, 12, 25, 15, 14, 24, 23, 26, 13, 12, 11, 21, 25, 25, 15, 26, 23, 10, 30, 12, 13, 15, 10, 18, 14, 13, 12, 7, 12, 14, 15, 12, 34, 23, 11, 12, 13, 24, 36, 25, 22, 8, 19, 28, 15, 24, 30, 20, 14, 12, 52, 11, 13, 21, 14, 8, 10, 8, 8, 28, 38, 8, 6, 11, 17, 10, 12, 21, 12, 11, 9, 17, 14, 16, 17, 25, 25, 9, 19, 15, 13, 20, 15, 50, 29, 23, 20, 15, 13, 18, 8, 19, 16, 21, 21, 11, 10, 16, 25, 14, 20, 26, 21, 21, 22, 10, 13, 17, 16, 29, 32, 14, 30, 30, 29, 18, 23, 28, 31, 22, 13, 16, 15, 15, 26, 13, 37, 16, 22, 8, 26, 34, 34, 18, 9, 10, 26, 23, 17, 18, 34, 18, 13, 16, 32, 21, 18, 33, 26, 15, 24, 16, 9, 18, 21, 69, 14, 20, 13, 15, 29, 38, 26, 12, 14, 14, 8, 8, 12, 41, 

In [ ]:
tour_feature_data = []
tour_label_data = []
for i in range(0,200):
  part_preprocess(tourism_ff[i],tour_feature_data,tour_label_data)


In [ ]:
#old data dis and tourism
dis_feature_data_1 = []
dis_label_data_1 = []
for i in range(len(disease_ff_1)):
  part_preprocess(disease_ff_1[i],dis_feature_data_1,dis_label_data_1)


tour_feature_data_1 = []
tour_label_data_1 = []
for i in range(len(tourism_ff_1)):
  part_preprocess(tourism_ff_1[i],tour_feature_data_1,tour_label_data_1)

In [ ]:
print(len(tour_feature_data))
print(len(tour_label_data))
print(tour_feature_data)
print(tour_label_data)

3158
3158
[['((', 'कावेरी', 'डेल्टा', 'के', '((', 'किसानों', 'की', '((', 'सिंचाई', 'आवश्यकता', 'की', '((', 'गंभीरता', 'को', '((', 'देखते', 'हुए', '((', 'तमिलनाडु', 'में', '((', 'सत्ताधारी', 'अन्नाद्रमुक', 'के', 'साथ', '((', 'विपक्ष', 'भी', '((', 'सक्रिय', '((', 'हो', 'गया', 'है', '((', '।'], ['((', 'उन्होंने', '((', 'शनिवार', 'को', '((', 'अपने', '((', 'प्रयासों', 'में', '((', 'तेजी', '((', 'लाते', 'हुए', '((', 'केंद्र', 'सरकार', 'से', '((', 'आग्रह', '((', 'किया', '((', 'कि', '((', 'वह', '((', 'कर्नाटक', 'से', '((', 'कावेरी', 'नदी', 'में', '((', 'पानी', '((', 'छुड़वाए', '((', '।'], ['((', 'द्रमुक', ',', '((', 'NULL', '((', 'कांग्रेस', 'समेत', '((', 'राज्य', 'के', '((', 'विपक्षी', 'गठबंधन', '((', 'व', '((', 'वामपंथी', 'पार्टियों', 'ने', '((', 'इस', 'मसले', 'पर', '((', '१०', 'जून', 'को', '((', 'कर्नाटक', 'के', '((', 'मुख्यमंत्री', '((', 'धरम', 'सिंह', 'से', '((', 'मिलने', 'के', 'लिए', '((', 'एक', 'प्रतिनिधिमंडल', '((', 'भेजने', 'का', '((', 'फैसला', '((', 'किया', 'है', '((', '।'], ['((', 'ज

In [ ]:
for i in range(200,len(tourism_ff)):
  part_preprocess(tourism_ff[i],tour_feature_data,tour_label_data)

In [ ]:
!jupyter notebook --NotebookApp.iopub_data_rate_limit=1e18

Traceback (most recent call last):
  File "/usr/local/bin/jupyter-notebook", line 8, in <module>
    sys.exit(main())
  File "/usr/local/lib/python2.7/dist-packages/jupyter_core/application.py", line 267, in launch_instance
    return super(JupyterApp, cls).launch_instance(argv=argv, **kwargs)
  File "/usr/local/lib/python2.7/dist-packages/traitlets/config/application.py", line 657, in launch_instance
    app.initialize(argv)
  File "</usr/local/lib/python2.7/dist-packages/decorator.pyc:decorator-gen-7>", line 2, in initialize
  File "/usr/local/lib/python2.7/dist-packages/traitlets/config/application.py", line 87, in catch_config_error
    return method(app, *args, **kwargs)
  File "/usr/local/lib/python2.7/dist-packages/notebook/notebookapp.py", line 1368, in initialize
    self.init_webapp()
  File "/usr/local/lib/python2.7/dist-packages/notebook/notebookapp.py", line 1188, in init_webapp
    self.http_server.listen(port, self.ip)
  File "/usr/local/lib/python2.7/dist-packages/torna

In [ ]:
def pos_tag_separater(listName,listName1):
  pos_data = []
  pos_label = []
  for i in range(len(listName)):
    pos_elem_lst = []
    pos_label_lst = []
    for j in range(len(listName[i])):
      if(listName[i][j] != "(("):
        pos_elem_lst.append(listName[i][j])
        pos_label_lst.append(listName1[i][j])
    pos_data.append(pos_elem_lst)
    pos_label.append(pos_label_lst)
  return (pos_data,pos_label)


In [ ]:
def chunk_tag_separater(listName,listName1):
  chunk_data = []
  chunk_label = []
  for i in range(len(listName)):
    chunk_elem_lst = []
    chunk_label_lst = []
    chunk = listName1[i][0]
    for j in range(len(listName[i])):
      if(listName[i][j] == "(("):
        chunk = listName1[i][j]
        m = 'B-'
      else:
        chunk_elem_lst.append(listName[i][j])
        chunk_label_lst.append(m+chunk)
        m='I-'
    chunk_data.append(chunk_elem_lst)
    chunk_label.append(chunk_label_lst)
  return (chunk_data,chunk_label)
        


In [ ]:
chunk_feature_dis,chunk_label_dis = chunk_tag_separater(dis_feature_data,dis_label_data)

In [ ]:
print(len(dis_feature_data[0]))
print(dis_label_data)

18
[['NP', 'NNC', 'NNP', 'VGNF', 'VM', 'VAUX', 'VGF', 'VM', 'BLK', 'INJ', 'NP', 'NNP', 'NP', 'WQ', 'VGF', 'VM', 'BLK', 'SYM'], ['NP', 'NNP', 'NP', 'NN', 'PSP', 'NP', 'NN', 'PSP', 'JJP', 'JJ', 'VGNF', 'VM', 'VGF', 'VM', 'NP', 'PRP', 'VGF', 'VM', 'VAUX', 'BLK', 'SYM'], ['NP', 'QF', 'JJ', 'NN', 'PSP', 'NP', 'PRP', 'NP', 'NN', 'VGF', 'VM', 'NULL__CCP', 'CC', 'NP', 'NN', 'NEGP', 'NEG', 'NULL__VGF', 'VM', 'BLK', 'SYM'], ['NP', 'NN', 'PSP', 'NST', 'PSP', 'NP', 'NN', 'VGF', 'VM', 'VAUX', 'VAUX', 'BLK', 'SYM'], ['NP', 'NNP', 'BLK', 'SYM', 'JJP', 'JJ', 'VGF', 'NEG', 'VM', 'NP', 'NN', 'PSP', 'NST', 'PSP', 'NP', 'NN', 'VGNN', 'VM', 'BLK', 'SYM'], ['NP', 'NNP', 'BLK', 'SYM', 'NEGP', 'NEG', 'BLK', 'SYM'], ['NP', 'PRP', 'RP', 'NP', 'NNC', 'SYM', 'NN', 'NP', 'NN', 'VGF', 'VM', 'VAUX', 'BLK', 'SYM'], ['NP', 'NNP', 'BLK', 'SYM', 'NP', 'NN', 'NP', 'PRP', 'NP', 'NN', 'PSP', 'NP', 'NN', 'VGF', 'VM', 'BLK', 'SYM'], ['NP', 'NNP', 'BLK', 'SYM', 'NP', 'NN', 'PSP', 'VGF', 'VM', 'VAUX', 'VAUX', 'NULL__CCP', 'CC'

In [ ]:
print(chunk_feature_dis)
print(chunk_label_dis)

[['इंस्पेक्टर', 'क्रान्तिलाल', 'गरजते', 'हुए', 'बोले', 'अरे', 'कौशल्ये', 'कहां', 'हो', '?'], ['कौशल्या', 'रसोई', 'से', 'डयोढी', 'पर', 'खड़ी', 'होकर', 'बोली', 'क्योंजी', 'डराते', 'हैं', '।'], ['इतनी', 'रौबीली', 'आवाज', 'में', 'ये', 'घर', 'है', 'NULL', 'थाना', 'नहीं', 'NULL', '।'], ['घर', 'के', 'बाहर', 'से', 'आवाज', 'देने', 'लगते', 'हो', '।'], ['क्रान्तिलाल', '-', 'अच्छा', 'नहीं', 'लगता', 'घर', 'के', 'बाहर', 'से', 'आवाज', 'देना', '।'], ['कौशल्या', '-', 'नहीं', '।'], ['ऐसे', 'तो', 'जेठ', '-', 'ससुर', 'आवाज', 'लगाते', 'हैं', '।'], ['क्रान्तिलाल', '-', 'मतलब', 'मुझमें', 'बदलाव', 'की', 'गुंजाइश', 'है', '।'], ['कौशल्या', '-', 'घर', 'में', 'आ', 'गये', 'हो', 'NULL', 'अब', 'बैठ', 'जाओ', '।'], ['मैं', 'चाय', 'पानी', 'लेकर', 'आती', 'हूं', '।'], ['क्रान्तिलाल', 'पानी', 'का', 'गिलास', 'थामते', 'हुए', 'बोले', 'कौशल्ये', 'कोई', 'आया', 'है', 'क्या', '?'], ['कौशल्या', '-', 'देखो', 'जासूसी', 'करना', 'बन्द', 'करो', '।'], ['चाय', '-', 'पानी', 'करो', 'NULL', 'नहाओ', 'धोओ', '।'], ['थके', 'मांदे', 'हो', '।'],

In [ ]:
pos_feature_dis , pos_label_dis = pos_tag_separater(dis_feature_data,dis_label_data)
pos_feature_tour , pos_label_tour = pos_tag_separater(tour_feature_data,tour_label_data)

In [ ]:
# prediction = pd.DataFrame(pos_feature_tour[:15088]).to_csv('train_articles.csv')
# prediction = pd.DataFrame(pos_feature_dis[:1700]).to_csv('train_conv.csv')
# prediction = pd.DataFrame(pos_feature_dis_1[:900]).to_csv('train_dis.csv')

# prediction = pd.DataFrame(pos_feature_tour_1[:2400]).to_csv('train_tour.csv')

# prediction = pd.DataFrame(pos_feature_tour[15088:]).to_csv('test_articles.csv')
# prediction = pd.DataFrame(pos_feature_dis[1700:]).to_csv('test_conv.csv')
# prediction = pd.DataFrame(pos_feature_dis_1[900:]).to_csv('test_dis.csv')

# prediction = pd.DataFrame(pos_feature_tour_1[2400:]).to_csv('test_tour.csv')

# prediction = pd.DataFrame(pos_label_tour[:15088]).to_csv('train_label_articles.csv')
# prediction = pd.DataFrame(pos_label_dis[:1700]).to_csv('train_label_conv.csv')
# prediction = pd.DataFrame(pos_label_dis_1[:900]).to_csv('train_label_dis.csv')

prediction = pd.DataFrame(pos_label_tour_1[:2400]).to_csv('train_label__tour.csv')

# prediction = pd.DataFrame(pos_label_tour[15088:]).to_csv('test_label_articles.csv')
# prediction = pd.DataFrame(pos_label_dis[1700:]).to_csv('test_label_conv.csv')
# prediction = pd.DataFrame(pos_label_dis_1[900:]).to_csv('test_label_dis.csv')

# prediction = pd.DataFrame(pos_label_tour_1[2400:]).to_csv('test_label_tour.csv')




In [ ]:

def char_featurizer(pos_feature_dis):
  char_feature = []
  for i in range(len(pos_feature_dis)):
    for j in range(min(len(pos_feature_dis[i]),52)):
      char_feature.append(list(pos_feature_dis[i][j]))
      
    
      
    if len(pos_feature_dis[i]) < 52 :
      for j in range(52-len(pos_feature_dis[i])):
        char_feature.append([])
  return (char_feature)


In [ ]:
char_pos_feature_dis = char_featurizer(pos_feature_dis)
char_pos_feature_tour = char_featurizer(pos_feature_tour)

In [ ]:
chunk_feature_dis_1,chunk_label_dis_1 = chunk_tag_separater(dis_feature_data_1,dis_label_data_1)
chunk_feature_tour_1,chunk_label_tour_1=chunk_tag_separater(tour_feature_data_1,tour_label_data_1)

pos_feature_dis_1 , pos_label_dis_1= pos_tag_separater(dis_feature_data_1,dis_label_data_1)
pos_feature_tour_1, pos_label_tour_1 = pos_tag_separater(tour_feature_data_1,tour_label_data_1)


char_pos_feature_dis_1 = char_featurizer(pos_feature_dis_1)
char_pos_feature_tour_1 = char_featurizer(pos_feature_tour_1)


## Model Without Transfer Learning 
**PosTagging model on hindi disease data**
# Preprocessed data

1.   pos_feature_dis
2.   pos_label_dis
3.   pos_feature_tour
4.   pos_label_tour
5.   char_pos_feature_dis
6.   char_pos_feature_tour



In [ ]:
char_tokenizer = Tokenizer(oov_token="<OOV>")

char_tokenizer.fit_on_texts((char_pos_feature_dis))
char_tokenizer.fit_on_texts((char_pos_feature_dis_1))
char_tokenizer.fit_on_texts((char_pos_feature_tour))
char_tokenizer.fit_on_texts((char_pos_feature_tour_1))

char_index = char_tokenizer.word_index

CHAR_MAX_LENGTH = len(max(char_pos_feature_dis_1,key=len))

CHAR_MAX_LENGTH = max(CHAR_MAX_LENGTH,len(max(char_pos_feature_dis,key=len)))

CHAR_MAX_LENGTH =max(CHAR_MAX_LENGTH,len(max(char_pos_feature_tour,key=len)))
CHAR_MAX_LENGTH = max(CHAR_MAX_LENGTH,len(max(char_pos_feature_tour_1,key=len)))

print(CHAR_MAX_LENGTH)


train_charword_sequences = char_tokenizer.texts_to_sequences(char_pos_feature_dis)
print(len(pos_feature_dis))
print(len(train_charword_sequences))
 



padded_charword_sequences_dis = pad_sequences(train_charword_sequences,padding='post',maxlen=CHAR_MAX_LENGTH,truncating="post")
#encoded = to_categorical(padded_charword_sequences_dis)
#padded_charword_sequences_dis=np.array(encoded,dtype="int")

print(padded_charword_sequences_dis)
print(char_pos_feature_dis)
print(len(char_index))

22
2196
114192
[[35 11 10 ...  0  0  0]
 [ 3  6  4 ...  0  0  0]
 [23  4 21 ...  0  0  0]
 ...
 [ 0  0  0 ...  0  0  0]
 [ 0  0  0 ...  0  0  0]
 [ 0  0  0 ...  0  0  0]]
[['इ', 'ं', 'स', '्', 'प', 'े', 'क', '्', 'ट', 'र'], ['क', '्', 'र', 'ा', 'न', '्', 'त', 'ि', 'ल', 'ा', 'ल'], ['ग', 'र', 'ज', 'त', 'े'], ['ह', 'ु', 'ए'], ['ब', 'ो', 'ल', 'े'], ['अ', 'र', 'े'], ['क', 'ौ', 'श', 'ल', '्', 'य', 'े'], ['क', 'ह', 'ा', 'ं'], ['ह', 'ो'], ['?'], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], ['क', 'ौ', 'श', 'ल', '्', 'य', 'ा'], ['र', 'स', 'ो', 'ई'], ['स', 'े'], ['ड', 'य', 'ो', 'ढ', 'ी'], ['प', 'र'], ['ख', 'ड', '़', 'ी'], ['ह', 'ो', 'क', 'र'], ['ब', 'ो', 'ल', 'ी'], ['क', '्', 'य', 'ो', 'ं', 'ज', 'ी'], ['ड', 'र', 'ा', 'त', 'े'], ['ह', 'ै', 'ं'], ['।'], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []

In [ ]:
print(padded_charword_sequences_dis.shape)

(114192, 22)


## tour charword data preprocessing

In [ ]:
# tour charword data preprocessing
train_charword_sequences_tour = char_tokenizer.texts_to_sequences(char_pos_feature_tour)
padded_charword_sequences_tour = pad_sequences(train_charword_sequences_tour,padding="post",maxlen=CHAR_MAX_LENGTH,truncating="post")


In [ ]:
padded_charword_sequences_tour = padded_charword_sequences_tour.reshape(-1,52,CHAR_MAX_LENGTH)
print(padded_charword_sequences_tour.shape)

(16998, 52, 22)


In [ ]:
print(padded_charword_sequences_dis.shape)


padded_charword_sequences_dis= padded_charword_sequences_dis.reshape(-1,52,CHAR_MAX_LENGTH)
# #CHAR_MAX_LENGTH
print(padded_charword_sequences_dis.shape)

(114192, 22)
(2196, 52, 22)


In [ ]:
print(padded_charword_sequences_dis.shape)

(2196, 52, 22)


In [ ]:
word_tokenizer = Tokenizer(oov_token="<OOV>")
word_tokenizer.fit_on_texts(pos_feature_dis)
word_tokenizer.fit_on_texts(pos_feature_dis_1)
word_tokenizer.fit_on_texts(pos_feature_tour)
word_tokenizer.fit_on_texts(pos_feature_tour_1)

word_index = word_tokenizer.word_index

train_word_sequences = word_tokenizer.texts_to_sequences(pos_feature_dis)
padded_word_sequences_dis = pad_sequences(train_word_sequences,padding='post',maxlen=52,truncating="post")

print(padded_word_sequences_dis.shape)

(2196, 52)


In [ ]:

print(padded_word_sequences_dis.shape)
print(pos_label_dis)


(2196, 52)
[['NNC', 'NNP', 'VM', 'VAUX', 'VM', 'INJ', 'NNP', 'WQ', 'VM', 'SYM'], ['NNP', 'NN', 'PSP', 'NN', 'PSP', 'JJ', 'VM', 'VM', 'PRP', 'VM', 'VAUX', 'SYM'], ['QF', 'JJ', 'NN', 'PSP', 'PRP', 'NN', 'VM', 'CC', 'NN', 'NEG', 'VM', 'SYM'], ['NN', 'PSP', 'NST', 'PSP', 'NN', 'VM', 'VAUX', 'VAUX', 'SYM'], ['NNP', 'SYM', 'JJ', 'NEG', 'VM', 'NN', 'PSP', 'NST', 'PSP', 'NN', 'VM', 'SYM'], ['NNP', 'SYM', 'NEG', 'SYM'], ['PRP', 'RP', 'NNC', 'SYM', 'NN', 'NN', 'VM', 'VAUX', 'SYM'], ['NNP', 'SYM', 'NN', 'PRP', 'NN', 'PSP', 'NN', 'VM', 'SYM'], ['NNP', 'SYM', 'NN', 'PSP', 'VM', 'VAUX', 'VAUX', 'CC', 'PRP', 'VM', 'VAUX', 'SYM'], ['PRP', 'NNC', 'NN', 'VM', 'VM', 'VAUX', 'SYM'], ['NNP', 'NN', 'PSP', 'NN', 'VM', 'VAUX', 'VM', 'NNP', 'PRP', 'VM', 'VAUX', 'WQ', 'SYM'], ['NNP', 'SYM', 'VM', 'NN', 'VM', 'JJ', 'VM', 'SYM'], ['NNC', 'SYM', 'NN', 'VM', 'CC', 'VMC', 'VM', 'SYM'], ['JJC', 'JJ', 'VM', 'SYM'], ['NN', 'PSP', 'NEG', 'VM', 'CC', 'PRP', 'NN', 'PSP', 'VM', 'VAUX', 'VAUX', 'SYM'], ['NST', 'PRP', 'NN', 

## tour word tokenization and padding sequences

In [ ]:

train_word_sequences_tour = word_tokenizer.texts_to_sequences(pos_feature_tour)
padded_word_sequences_tour = pad_sequences(train_word_sequences_tour,maxlen=52,padding="post",truncating="post")
print(padded_word_sequences_tour.shape)
print(pos_label_tour)

(16998, 52)
[['NNPC', 'NNP', 'PSP', 'NN', 'PSP', 'NNC', 'NN', 'PSP', 'NN', 'PSP', 'VM', 'VAUX', 'NNP', 'PSP', 'JJ', 'NNP', 'PSP', 'NST', 'NN', 'RP', 'JJ', 'VM', 'VAUX', 'VAUX', 'SYM'], ['PRP', 'NNP', 'PSP', 'PRP', 'NN', 'PSP', 'NN', 'VM', 'VAUX', 'NNPC', 'NNP', 'PSP', 'NN', 'VM', 'CC', 'PRP', 'NNP', 'PSP', 'NNP', 'NN', 'PSP', 'NN', 'VM', 'SYM'], ['NNP', 'SYM', 'CC', 'NNP', 'PSP', 'NN', 'PSP', 'JJ', 'NN', 'CC', 'NNC', 'NN', 'PSP', 'DEM', 'NN', 'PSP', 'NNPC', 'NNP', 'PSP', 'NNP', 'PSP', 'NNP', 'NNPC', 'NNP', 'PSP', 'VM', 'PSP', 'PSP', 'QC', 'NN', 'VM', 'PSP', 'NN', 'VM', 'VAUX', 'SYM'], ['CC', 'NN', 'PSP', 'NNP', 'NNP', 'PSP', 'NNP', 'NNPC', 'NNP', 'PSP', 'NN', 'VM', 'VAUX', 'CC', 'NNPC', 'NNPC', 'NNP', 'PSP', 'NN', 'VM', 'VAUX', 'CC', 'NNPC', 'NNPC', 'NNPC', 'NNP', 'PSP', 'JJ', 'NN', 'PSP', 'NN', 'PSP', 'NN', 'PSP', 'NNC', 'SYM', 'NN', 'VM', 'VAUX', 'SYM'], ['NNP', 'PSP', 'DEM', 'NN', 'PSP', 'NNP', 'PSP', 'QC', 'NN', 'VM', 'VAUX', 'SYM'], ['NST', 'SYM', 'NNP', 'SYM', 'NNP', 'SYM', 'NNP'

In [ ]:

label_tokenizer = Tokenizer() # have to change these to perform cross task transfer learning
label_tokenizer.fit_on_texts(pos_label_dis)
label_index = label_tokenizer.word_index
train_label_sequences = label_tokenizer.texts_to_sequences(pos_label_dis)
padded_label_sequence = pad_sequences(train_label_sequences,padding="post",maxlen=52,truncating="post")
print(padded_label_sequence)
print(padded_label_sequence.shape)
print(label_index)

[[11  7  2 ...  0  0  0]
 [ 7  1  3 ...  0  0  0]
 [16  9  1 ...  0  0  0]
 ...
 [ 7  4  1 ...  0  0  0]
 [ 6  6  1 ...  0  0  0]
 [ 1  6 15 ...  0  0  0]]
(2196, 52)
{'nn': 1, 'vm': 2, 'psp': 3, 'sym': 4, 'vaux': 5, 'prp': 6, 'nnp': 7, 'rp': 8, 'jj': 9, 'cc': 10, 'nnc': 11, 'neg': 12, 'nst': 13, 'wq': 14, 'dem': 15, 'qf': 16, 'qc': 17, 'inj': 18, 'rb': 19, 'rdp': 20, 'jjc': 21, 'vmc': 22, 'qo': 23, 'nnpc': 24, 'unk': 25, 'intf': 26, 'rbc': 27, 'prpc': 28, 'qcc': 29, 'injc': 30, 'nstc': 31, 'qfc': 32, 'ech': 33}


## tour label tokenization and padding sequences

In [ ]:
label_tokenizer1 = Tokenizer()
label_tokenizer1.fit_on_texts(pos_label_tour)
label_index1 = label_tokenizer1.word_index
train_label_sequences_tour = label_tokenizer1.texts_to_sequences(pos_label_tour)
padded_label_sequence_tour = pad_sequences(train_label_sequences_tour,padding="post",maxlen=52,truncating="post")
print(padded_label_sequence_tour.shape)



(16998, 52)


In [ ]:


padded_label_sequence_one_hot_tour = np.zeros(padded_label_sequence_tour.shape+(len(label_index1)+1,))
for i in range(padded_label_sequence_tour.shape[0]):
  for j in range(padded_label_sequence_tour.shape[1]):
    t = padded_label_sequence_tour[i,j]
    padded_label_sequence_one_hot_tour[i,j,t] = 1
print(padded_label_sequence_one_hot_tour.shape)



for i in label_index:
  if i not in label_index1:
    print(i)


label_final = list(label_index1)
for i in list(label_index):
  if i not in list(label_index1):
    label_final.append(i)
print(len(label_final))    

label_final_articles_conv= label_final


label_tokenizer_final = Tokenizer()
label_tokenizer_final.fit_on_texts([label_final])
label_final_index = label_tokenizer_final.word_index
train_label_tour = label_tokenizer_final.texts_to_sequences(pos_label_tour)
padded_label_sequence_tour_final = pad_sequences(train_label_tour,maxlen=52,padding="post",truncating="post")
train_label_dis = label_tokenizer_final.texts_to_sequences(pos_label_dis)
padded_label_sequence_dis_final = pad_sequences(train_label_dis,maxlen=52,padding="post",truncating="post")


pos_label_conversation= pos_label_dis
pos_label_articles= pos_label_tour



def one_hotencoding(listName,label_final_index):
  arr = np.zeros(listName.shape+(len(label_final_index)+1,))
  print(arr.shape)
  for i in range(listName.shape[0]):
    for j in range(listName.shape[1]):
      k = listName[i,j]
      arr[i,j,k] = 1
  return arr


padded_label_sequence_one_hot_dis = one_hotencoding(padded_label_sequence_dis_final,label_final_index)
padded_label_sequence_tour_final_one_hot = one_hotencoding(padded_label_sequence_tour_final,label_final_index)

print(padded_label_sequence_tour_final_one_hot.shape)




train_padded_word_sequences_conv=padded_word_sequences_dis[:1700]
train_padded_charword_sequences_conv=padded_charword_sequences_dis[:1700]
test_padded_word_sequences_conv=padded_word_sequences_dis[1700:]
test_padded_charword_sequences_conv=padded_charword_sequences_dis[1700:]
train_padded_label_sequence_one_hot_conv=padded_label_sequence_one_hot_dis[:1700]
test_padded_label_sequence_one_hot_conv=padded_label_sequence_one_hot_dis[1700:]
print(train_padded_charword_sequences_conv.shape)






train_padded_word_sequences_articles=padded_word_sequences_tour[:15088]
train_padded_charword_sequences_articles=padded_charword_sequences_tour[:15088]
test_padded_word_sequences_articles=padded_word_sequences_tour[15088:]
test_padded_charword_sequences_articles=padded_charword_sequences_tour[15088:]
train_padded_label_sequence_one_hot_articles=padded_label_sequence_tour_final_one_hot[:15088]
test_padded_label_sequence_one_hot_articles=padded_label_sequence_tour_final_one_hot[15088:]

print(len(label_final))



(16998, 52, 38)
injc
ech
39
(2196, 52, 40)
(16998, 52, 40)
(16998, 52, 40)
(1700, 52, 22)
39


In [ ]:
 #old data preprocessing 
#final Disease and Tourism data


train_charword_sequences= char_tokenizer.texts_to_sequences(char_pos_feature_dis_1)

 
padded_charword_sequences_dis = pad_sequences(train_charword_sequences,padding='post',maxlen=CHAR_MAX_LENGTH,truncating="post")


# tour charword data preprocessing
train_charword_sequences_tour = char_tokenizer.texts_to_sequences(char_pos_feature_tour_1)
padded_charword_sequences_tour = pad_sequences(train_charword_sequences_tour,padding="post",maxlen=CHAR_MAX_LENGTH,truncating="post")


padded_charword_sequences_tour = padded_charword_sequences_tour.reshape(-1,52,CHAR_MAX_LENGTH)
padded_charword_sequences_dis= padded_charword_sequences_dis.reshape(-1,52,CHAR_MAX_LENGTH)



train_word_sequences = word_tokenizer.texts_to_sequences(pos_feature_dis_1)
padded_word_sequences_dis = pad_sequences(train_word_sequences,padding='post',maxlen=52,truncating="post")


train_word_sequences_tour = word_tokenizer.texts_to_sequences(pos_feature_tour_1)
padded_word_sequences_tour = pad_sequences(train_word_sequences_tour,maxlen=52,padding="post",truncating="post")


label_tokenizer = Tokenizer() # have to change these to perform cross task transfer learning
label_tokenizer.fit_on_texts(pos_label_dis_1)
label_index = label_tokenizer.word_index

train_label_sequences = label_tokenizer.texts_to_sequences(pos_label_dis_1)
padded_label_sequence = pad_sequences(train_label_sequences,padding="post",maxlen=52,truncating="post")




label_tokenizer1 = Tokenizer()
label_tokenizer1.fit_on_texts(pos_label_tour_1)
label_index1 = label_tokenizer1.word_index

train_label_sequences_tour = label_tokenizer1.texts_to_sequences(pos_label_tour_1)
padded_label_sequence_tour = pad_sequences(train_label_sequences_tour,padding="post",maxlen=52,truncating="post")




padded_label_sequence_one_hot_tour = np.zeros(padded_label_sequence_tour.shape+(len(label_index1)+1,))
for i in range(padded_label_sequence_tour.shape[0]):
  for j in range(padded_label_sequence_tour.shape[1]):
    t = padded_label_sequence_tour[i,j]
    padded_label_sequence_one_hot_tour[i,j,t] = 1



label_final = list(label_index1)
for i in list(label_index):
  if i not in list(label_index1):
    label_final.append(i)
print(len(label_final))    
#final label dis and tour
label_final_dis_tour= label_final



label_tokenizer_final = Tokenizer()
label_tokenizer_final.fit_on_texts([label_final])
label_final_index = label_tokenizer_final.word_index
train_label_tour = label_tokenizer_final.texts_to_sequences(pos_label_tour_1)
padded_label_sequence_tour_final = pad_sequences(train_label_tour,maxlen=52,padding="post",truncating="post")
train_label_dis = label_tokenizer_final.texts_to_sequences(pos_label_dis_1)
padded_label_sequence_dis_final = pad_sequences(train_label_dis,maxlen=52,padding="post",truncating="post")




def one_hotencoding(listName,label_final_index):
  arr = np.zeros(listName.shape+(len(label_final_index)+1,))
  print(arr.shape)
  for i in range(listName.shape[0]):
    for j in range(listName.shape[1]):
      k = listName[i,j]
      arr[i,j,k] = 1
  return arr


padded_label_sequence_one_hot_dis = one_hotencoding(padded_label_sequence_dis_final,label_final_index)
padded_label_sequence_tour_final_one_hot = one_hotencoding(padded_label_sequence_tour_final,label_final_index)


train_padded_word_sequences_dis=padded_word_sequences_dis[:900]
train_padded_charword_sequences_dis=padded_charword_sequences_dis[:900]
test_padded_word_sequences_dis=padded_word_sequences_dis[900:]
test_padded_charword_sequences_dis=padded_charword_sequences_dis[900:]
train_padded_label_sequence_one_hot_dis=padded_label_sequence_one_hot_dis[:900]
test_padded_label_sequence_one_hot_dis=padded_label_sequence_one_hot_dis[900:]








print(test_padded_charword_sequences_dis.shape)

train_padded_word_sequences_tour=padded_word_sequences_tour[:2400]
train_padded_charword_sequences_tour=padded_charword_sequences_tour[:2400]
test_padded_word_sequences_tour=padded_word_sequences_tour[2400:]
test_padded_charword_sequences_tour=padded_charword_sequences_tour[2400:]
train_padded_label_sequence_one_hot_tour=padded_label_sequence_tour_final_one_hot[:2400]
test_padded_label_sequence_one_hot_tour=padded_label_sequence_tour_final_one_hot[2400:]



print(train_padded_label_sequence_one_hot_tour.shape)



53
(1494, 52, 54)
(3022, 52, 54)
(594, 52, 22)
(2400, 52, 54)


# All domain mix ***data***

In [ ]:
label_all_domain_mix= label_final_dis_tour

for i in list(label_final_articles_conv):
  if i not in list(label_final_dis_tour):
    label_all_domain_mix.append(i)


print(len(label_all_domain_mix))



label_tokenizer_mix = Tokenizer()
label_tokenizer_mix.fit_on_texts([label_all_domain_mix])
label_final_mix_index = label_tokenizer_mix.word_index

train_label_tour = label_tokenizer_mix.texts_to_sequences(pos_label_tour_1)
padded_label_sequence_tour_final = pad_sequences(train_label_tour,maxlen=52,padding="post",truncating="post")

train_label_dis = label_tokenizer_final.texts_to_sequences(pos_label_dis_1)
padded_label_sequence_dis_final = pad_sequences(train_label_dis,maxlen=52,padding="post",truncating="post")

train_label_articles = label_tokenizer_mix.texts_to_sequences(pos_label_tour)
padded_label_sequence_articles_final = pad_sequences(train_label_articles,maxlen=52,padding="post",truncating="post")

train_label_conv = label_tokenizer_final.texts_to_sequences(pos_label_dis)
padded_label_sequence_conv_final = pad_sequences(train_label_conv,maxlen=52,padding="post",truncating="post")





def one_hotencoding(listName,label_final_index):
  arr = np.zeros(listName.shape+(len(label_final_index)+1,))
  print(arr.shape)
  for i in range(listName.shape[0]):
    for j in range(listName.shape[1]):
      k = listName[i,j]
      arr[i,j,k] = 1
  return arr


all_domains_padded_label_sequence_dis_final_one_hot  = one_hotencoding(padded_label_sequence_dis_final,label_all_domain_mix)
all_domains_padded_label_sequence_tour_final_one_hot = one_hotencoding(padded_label_sequence_tour_final,label_all_domain_mix)
all_domains_padded_label_sequence_conversation_final_one_hot = one_hotencoding(padded_label_sequence_conv_final,label_all_domain_mix)
all_domains_padded_label_sequence_articles_final_one_hot = one_hotencoding(padded_label_sequence_articles_final,label_all_domain_mix)








#Disease all domain data

all_domains_train_padded_label_sequence_one_hot_dis=   all_domains_padded_label_sequence_dis_final_one_hot [:900]
all_domains_test_padded_label_sequence_one_hot_dis=    all_domains_padded_label_sequence_dis_final_one_hot [900:]




#tourism all domain data

all_domains_train_padded_label_sequence_one_hot_tour=  all_domains_padded_label_sequence_tour_final_one_hot[:2400]
all_domains_test_padded_label_sequence_one_hot_tour=   all_domains_padded_label_sequence_tour_final_one_hot[2400:]


#articles all domain data

all_domains_train_padded_label_sequence_one_hot_articles=all_domains_padded_label_sequence_articles_final_one_hot[:15088]
all_domains_test_padded_label_sequence_one_hot_articles=all_domains_padded_label_sequence_articles_final_one_hot[15088:]

#coversation all domain data

all_domains_train_padded_label_sequence_one_hot_conv=  all_domains_padded_label_sequence_conversation_final_one_hot[:1700]
all_domains_test_padded_label_sequence_one_hot_conv=   all_domains_padded_label_sequence_conversation_final_one_hot[1700:]

print(train_padded_charword_sequences_conv.shape)





80
(1494, 52, 81)
(3022, 52, 81)
(2196, 52, 81)
(16998, 52, 81)
(1700, 52, 22)


In [ ]:
import pandas as pd

prediction = pd.DataFrame(label_all_domain_mix).to_csv('label_all_domains.csv')


# ***MODEL LAYERS***

In [ ]:
prediction =asarray(all_domains_test_padded_label_sequence_one_hot_conv.argmax(-1))
print(prediction[0])
prediction = pd.DataFrame(prediction).to_csv('all_domains_test_padded_label_sequence_one_hot_conv.csv')

NameError: ignored

In [ ]:
print(all_domains_train_padded_label_sequence_one_hot_tour[0][0])
print(padded_label_sequence_one_hot_tour[0][0])

[0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]


In [ ]:
def pretrained_embedding_layer(word_to_vec_map1,word_to_vec_map2,word_to_index):
  vocab_len = len(word_to_index) + 1
  # emb_dim1 = word_to_vec_map1["और"].shape[0]
  # emb_dim2 = word_to_vec_map2["और"].shape[0]
  emb_matrix = np.zeros((vocab_len,100))

  embedding_layer = Embedding(vocab_len,100,input_length=52)

  
  return embedding_layer

In [ ]:
!pip install git+https://www.github.com/keras-team/keras-contrib.git

  Cloning https://www.github.com/keras-team/keras-contrib.git to /tmp/pip-req-build-3mfx_8vo
  Running command git clone -q https://www.github.com/keras-team/keras-contrib.git /tmp/pip-req-build-3mfx_8vo
  Created wheel for keras-contrib: filename=keras_contrib-2.0.8-cp36-none-any.whl size=101066 sha256=7897e770d9141fb694ea58098254fb8e0f02afa284d0889c5af53ff1e92e8d97
  Stored in directory: /tmp/pip-ephem-wheel-cache-fqbamj3j/wheels/11/27/c8/4ed56de7b55f4f61244e2dc6ef3cdbaff2692527a2ce6502ba
Successfully built keras-contrib


In [ ]:
! pip install git+https://github.com/howl-anderson/tf_crf_layer.git

  Cloning https://github.com/howl-anderson/tf_crf_layer.git to /tmp/pip-req-build-sysi2_lt
  Running command git clone -q https://github.com/howl-anderson/tf_crf_layer.git /tmp/pip-req-build-sysi2_lt
     |████████████████████████████████| 71kB 3.2MB/s 
     |████████████████████████████████| 71kB 7.1MB/s 
     |████████████████████████████████| 317kB 17.2MB/s 
     |████████████████████████████████| 225kB 23.2MB/s 
  Created wheel for tf-crf-layer: filename=tf_crf_layer-0.2.5-py2.py3-none-any.whl size=22549 sha256=a326e3f277259c27507676d65b196d5967b5f996cbc91a926b6a0cd5c912b437
  Stored in directory: /tmp/pip-ephem-wheel-cache-ks9q1212/wheels/30/3f/a5/757896c44f46f33aaa94c6a863a03ff9cb739eb2688397a1e4
  Created wheel for pyahocorasick: filename=pyahocorasick-1.4.0-cp36-cp36m-linux_x86_64.whl size=81700 sha256=079e63339ab5605d7145c5e12f1431c822314e4284abb6bf591590a8c48f15a7
  Stored in directory: /root/.cache/pip/wheels/0a/90/61/87a55f5b459792fbb2b7ba6b31721b06ff5cf6bde541b40994
Succes

In [ ]:
from tf_crf_layer.layer import CRF

In [ ]:
from tensorflow.keras.layers import Flatten,GRUCell
from tensorflow.keras.layers import GRU,LSTM
import numpy as np
from tensorflow.keras.models import Model


In [ ]:
from tensorflow.keras.layers import RepeatVector,concatenate,Dot,Lambda
!pip install keras-self-attention
# from keras_contrib.losses import crf_loss
# from tensorflow.keras_contrib.metrics import crf_viterbi_accuracy
from tensorflow.keras.layers import Reshape
# from tf_crf_layer.loss import crf_loss
# from tf_crf_layer.metrics import crf_accuracy

  Created wheel for keras-self-attention: filename=keras_self_attention-0.47.0-cp36-none-any.whl size=17289 sha256=b0cd06958dc2d79252d5fd0ed2e4c9202fc3e9dbaff9e24a152ab7968d9b771a
  Stored in directory: /root/.cache/pip/wheels/70/87/01/76c703d5401b65e323927c1fdc665f3fb143282ff67d71e859
Successfully built keras-self-attention


CHAR CNN

In [ ]:

def charcnn(char_index,block):
    vocab_size = len(char_index)+1
    conv_layers = [[64,3,3],
                   [128,3,-1]]
    dropout_p = 0.3
    num_of_classes = 16
    embedding_size = 30

    fully_connected_layers = [128, 64]
    #print(block)
   # char_sequence = char_vectorizer.texts_to_sequences(block)
  #  char_padded_sequence = pad_sequences(char_sequences,maxlen=CHAR_MAX_LENGTH,padding='post',truncating='post')           
    
    embedding_layer = Embedding(vocab_size,embedding_size,input_length=CHAR_MAX_LENGTH)
  
    x = embedding_layer(block)
    for filter_num, filter_size, pooling_size in conv_layers:
        x = Conv1D(filter_num, filter_size)(x)
        x = Activation('relu')(x)
        if pooling_size != -1:
            x = MaxPooling1D(pool_size=pooling_size)(x)  
    x = Flatten()(x)
    for dense_size in fully_connected_layers:
        x = Dense(dense_size, activation='relu')(x)
        x = Dropout(dropout_p)(x)
    # Output Layer
    predictions = Dense(num_of_classes, activation='relu')(x)
    return predictions

In [ ]:

def moving_sum(x, back, forward):
    """Compute the moving sum of x over a window with the provided bounds.

    x is expected to be of shape (batch_size, sequence_length).
    The returned tensor x_sum is computed as
    x_sum[i, j] = x[i, j - back] + ... + x[i, j + forward]
    """
    # Moving sum is computed as a carefully-padded 1D convolution with ones
    print(x.shape)
    print(x)
    m = x.shape[2]
    x_padded = tf.pad(x, [[0, 0], [back, forward],[0,0]])
    # Add a "channel" dimension
    print(x_padded.shape)
    #x_padded = tf.expand_dims(x_padded, -1)
    print(x_padded.shape)
    # Construct filters
    filters = tf.ones((back + forward + 1,m,1))
    print(filters.shape)
    x_sum = tf.nn.conv1d(x_padded, filters, 1, padding='VALID')
    print(x_sum.shape)
    # Remove channel dimension
    return x_sum
def efficient_chunkwise_attention(chunk_size, emit_probs, softmax_logits):
    """Compute chunkwise attention distribution efficiently by clipping logits."""
    # Shift logits to avoid overflow
    softmax_logits -= tf.reduce_max(softmax_logits, 1, keepdims=True)
    print(softmax_logits.shape)
    # Limit the range for numerical stability
    softmax_exp = tf.exp(softmax_logits)
    print(softmax_exp)
    softmax_exp = tf.maximum(softmax_exp, 1e-5)
    print(softmax_exp)
    # Compute chunkwise softmax denominators
    softmax_denominators = moving_sum(softmax_exp, chunk_size - 1, 0)
    # Compute \beta_{i, :}. emit_probs are \alpha_{i, :}.
    probs = softmax_exp * moving_sum(emit_probs / softmax_denominators, 0, chunk_size - 1)
    return probs

In [ ]:
import tensorflow as tf

In [ ]:
print(CHAR_MAX_LENGTH)

22


In [ ]:
def CrossDomainChunk(word_to_vec_map, word_to_vec_map1, word_to_index,num_of_label):
  input_shape = (52,)
  input_shape1 = (52,CHAR_MAX_LENGTH)

  sentence_indices = Input(shape=input_shape,dtype='int32',name='input')
  embedding_layer = pretrained_embedding_layer(word_to_vec_map,word_to_vec_map1 ,word_to_index)
  embeddings = embedding_layer(sentence_indices)

  sentence_word = Input(shape=input_shape1,name='input1')
  char_feat = []
  for t in range(52):
    sentence_word_x = Lambda(lambda x : x[:,t,:])(sentence_word)
#    sentence_word_x = Reshape((1,))(sentence_word_x)
    char_feat.append(charcnn(char_index,sentence_word_x))
  print(len(char_feat))
  print(char_feat[0].shape)
  print(embeddings.shape)
  char_feat_tensor = Lambda(lambda x : K.stack(x,axis=1))(char_feat)
  print(char_feat_tensor.shape)
 
  mixed_embeddings = Concatenate()([embeddings,char_feat_tensor])

  print(mixed_embeddings)
  X = Bidirectional(GRU(units=128,return_sequences=True))(mixed_embeddings)
  X = Dropout(rate=0.5)(X)

  print(X.shape)
  chunk_list = Lambda(lambda x : efficient_chunkwise_attention(10,0.6,x))(X)
 
  X = Bidirectional(GRU(units=128,return_sequences=True))(chunk_list)
  print(X.shape)
  X = Dropout(rate=0.5)(X)
  # crf = CRF(num_of_label,sparse_target=False, name='crf')

  # X=(crf)(X)
  # outputs=X

  # X= Dense(num_of_label,activation='softmax')(X)

  X = Dense(units=num_of_label)(X)
  X= Activation('softmax')(X)
 
  model = Model(inputs=[sentence_indices,sentence_word],outputs=X)
  return model

In [ ]:
def CrossDomain_base(word_to_vec_map, word_to_vec_map1, word_to_index,num_of_label):
  input_shape = (52,)
  input_shape1 = (52,CHAR_MAX_LENGTH)

  sentence_indices = Input(shape=input_shape,dtype='int32',name='input')
  embedding_layer = pretrained_embedding_layer(word_to_vec_map,word_to_vec_map1 ,word_to_index)
  embeddings = embedding_layer(sentence_indices)

  sentence_word = Input(shape=input_shape1,name='input1')
  char_feat = []
  for t in range(52):
    sentence_word_x = Lambda(lambda x : x[:,t,:])(sentence_word)
#    sentence_word_x = Reshape((1,))(sentence_word_x)
    char_feat.append(charcnn(char_index,sentence_word_x))
  print(len(char_feat))
  print(char_feat[0].shape)
  print(embeddings.shape)
  char_feat_tensor = Lambda(lambda x : K.stack(x,axis=1))(char_feat)
  print(char_feat_tensor.shape)

  
  mixed_embeddings = Concatenate()([embeddings,char_feat_tensor])

  print(mixed_embeddings)
  X = Bidirectional(GRU(units=128,return_sequences=True))(mixed_embeddings)

  X = Bidirectional(GRU(units=128,return_sequences=True))(X)
  print(X.shape)
  X = Dropout(rate=0.5)(X)
  print(X.shape)
  X = Bidirectional(GRU(units=128,return_sequences=True))(X)
  print(X.shape)
  X = Dropout(rate=0.5)(X)
  print(X.shape)
 

  X = Dense(units=num_of_label)(X)
  X= Activation('softmax')(X)
  print(X.shape)

  model = Model(inputs=[sentence_indices,sentence_word],outputs=X)
  return model

In [ ]:
def CrossDomain(ccnum_of_label):
  input_shape = (52,)
  input_shape1 = (52,CHAR_MAX_LENGTH)

  sentence_indices = Input(shape=input_shape,dtype='int32')
  embedding_layer = pretrained_embedding_layer(word_to_vec_map,word_to_vec_map1 ,word_to_index)
  embeddings = embedding_layer(sentence_indices)

  sentence_word = Input(shape=input_shape1)
  char_feat = []
  for t in range(52):
    sentence_word_x = Lambda(lambda x : x[:,t,:])(sentence_word)
#    sentence_word_x = Reshape((1,))(sentence_word_x)
    char_feat.append(charcnn(char_index,sentence_word_x))
  print(len(char_feat))
  print(char_feat[0].shape)
  print(embeddings.shape)
  char_feat_tensor = Lambda(lambda x : K.stack(x,axis=1))(char_feat)
  print(char_feat_tensor.shape)

  
  mixed_embeddings = Concatenate()([embeddings,char_feat_tensor])

  print(mixed_embeddings)
  X = Bidirectional(GRU(units=128,return_sequences=True))(mixed_embeddings)
  X = Dropout(rate=0.5)(X)


  print(X.shape)
  X = (SeqSelfAttention(attention_type=SeqSelfAttention.ATTENTION_TYPE_MUL,
					  kernel_regularizer=keras.regularizers.l2(1e-4),
					  bias_regularizer=keras.regularizers.l1(1e-4),
					  attention_regularizer_weight=1e-4,
					  name='Attention'))(X)
  
  
  
  print(X.shape)
  X = Bidirectional(GRU(units=128,return_sequences=True))(X)
  print(X.shape)
  X = Dropout(rate=0.5)(X)
  # crf1 = CRF(40,sparse_target=False, name='crf1'
  # X= Dense(num_of_label,activation='softmax')(X)

  crf = CRF(num_of_label,sparse_target=False, name='crf')

  X=(crf)(X)
  outputs=X
  

  model = Model(inputs=[sentence_indices,sentence_word],outputs=X)
  return model

In [ ]:
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping
opt = Adam(lr=0.02, beta_1=0.9, beta_2=0.999, decay=0.01)
model = CrossDomainChunk({},{},word_index,81)
model.compile(optimizer=opt, loss='categorical_crossentropy', metrics=['accuracy']) 

es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=15)

print(model.summary())


Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
If using Keras pass *_constraint arguments to layers.
52
(?, 16)
(?, 52, 100)
(?, 52, 16)
Tensor("concatenate/concat:0", shape=(?, 52, 116), dtype=float32)
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
(?, 52, 256)
(?, 52, 256)
Tensor("lambda_53/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("lambda_53/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("lambda_53/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("lambda_53/truediv:0", shape=(?, 52, 1), dtype=

## training on tour data and saving weights to perform transfer learining

# ***layer_to_layer_testing***

In [ ]:
def transfer_weights(layer_num,model_1,model_2):

  for i in layer_num:
    model_1.layers[-i].set_weights(model_2.layers[-i].get_weights())

def repo(test_data,name,adv_model):
  y_pre= adv_model.predict(test_data[0])

  y_pred=y_pre.argmax(-1)
  prediction =asarray(y_pred)
  print(prediction[0])
  prediction = pd.DataFrame(prediction).to_csv(name)

  classification_report_org(test_data[1].argmax(-1),y_pred,label_all_domain_mix)




def tf_partial_layers(layer_num,file_name,model_s_data,model_t_data,lr_s,lr_t,epochs_s,epochs_t,test_data,name):
  es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=15)

  opt_s = Adam(lr_s, beta_1=0.9, beta_2=0.999, decay=0.01)
  model_s = CrossDomainChunk({},{},word_index,81)
  model_s.compile(optimizer=opt_s, loss='categorical_crossentropy', metrics=['accuracy']) 

  if file_name!="":
    model_s.load_weights(file_name)
  else :  
    history=model_s.fit(model_s_data[0],model_s_data[1],validation_split=0.2,epochs=epochs_s,batch_size=32,callbacks=[es])
    model_s.save_weights('temp.h5')



  
  opt_t = Adam(lr_t, beta_1=0.9, beta_2=0.999, decay=0.01)
  model_t = CrossDomainChunk({},{},word_index,81)
  model_t.compile(optimizer=opt_t, loss='categorical_crossentropy', metrics=['accuracy']) 



  transfer_weights(layer_num,model_s,model_t)


  
  history=model_s.fit(model_t_data[0],model_t_data[1],validation_split=0.2,epochs=epochs_t,batch_size=32,callbacks=[es])
  model_name= name +'.h5'
  model_s.save_weights(model_name)

  csv_name= name +'.csv'
  repo(test_data,csv_name,model_s)












In [ ]:
layer_num=[6,7,8]
file_name=""
model_s_data=[[train_padded_word_sequences_tour,train_padded_charword_sequences_tour],all_domains_train_padded_label_sequence_one_hot_tour]
model_t_data=[[train_padded_word_sequences_dis,train_padded_charword_sequences_dis],all_domains_train_padded_label_sequence_one_hot_dis]
epochs_s=50
epochs_t=100
lr_s=0.01
lr_t=0.01
test_data=[[test_padded_word_sequences_conv,test_padded_charword_sequences_conv],all_domains_test_padded_label_sequence_one_hot_conv]
name_for_saving="mocha_cd_tour_dis"

In [ ]:
repo(test_data,'dd',model)

In [ ]:
tf_partial_layers(layer_num,file_name,model_s_data,model_t_data,lr_s,lr_t,epochs_s,epochs_t,test_data,name_for_saving)

In [ ]:

history=model.fit([train_padded_word_sequences_conv,train_padded_charword_sequences_conv],all_domains_train_padded_label_sequence_one_hot_conv,validation_split=0.2,epochs=100,batch_size=32,callbacks=[es])

In [ ]:

history=model.fit([train_padded_word_sequences_dis,train_padded_charword_sequences_dis],all_domains_train_padded_label_sequence_one_hot_dis,validation_split=0.2,epochs=100,batch_size=32,callbacks=[es])

In [ ]:
model.evaluate([test_padded_word_sequences_dis,test_padded_charword_sequences_dis],all_domains_test_padded_label_sequence_one_hot_dis)

In [ ]:
model.save_weights("base_cd_conv_dis.h5")

In [ ]:
y_pred= model.predict([test_padded_word_sequences_dis,test_padded_charword_sequences_dis])
y_pred=y_pred.argmax(-1)
prediction =asarray(y_pred)

prediction = pd.DataFrame(prediction).to_csv("prediction_base_conv_dis")

classification_report_org(all_domains_test_padded_label_sequence_one_hot_dis.argmax(-1),y_pred,label_all_domain_mix)


In [ ]:
repo(test_data,"dd",model)

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
from google.colab import files
files.download("/content/dis_postagging_without_tl.h5")

## preprocessing for cross domain transfer learning

In [ ]:

history = model.fit([padded_word_sequences_tour,padded_charword_sequences_tour,s0,c0],
          padded_label_sequence_tour_final_one_hot,validation_split=0.2,epochs=100,batch_size=32)


In [ ]:
model.save_weights('tour_postagging_final_tl.h5')

In [ ]:
files.download('/content/tour_postagging_final_tl.h5')

In [ ]:
acc = history.history['acc']
val_acc = history.history['val_acc']
loss = history.history['loss']
val_loss = history.history['val_loss']
plt.plot(acc)
plt.plot(val_acc)
plt.xlabel("no of epochs")
plt.ylabel("train accuracy and validation accuracy")
plt.legend(["train acc","validation acc"],loc='upper right')
plt.title("accuray vs validation accuracy for transfer learning on tour postagging data ")
plt.savefig("tour_for_tl_acc.png")
plt.show()
files.download("/content/tour_for_tl_acc.png")

In [ ]:
plt.plot(loss)
plt.plot(val_loss)
plt.xlabel("no of epochs")
plt.ylabel("train loss and validation loss")
plt.legend(["train loss","validation loss"],loc='upper right')
plt.title("train loss vs validation loss for transfer learning on tour postagging data ")
plt.savefig("tour_for_tl_loss.png")
plt.show()
files.download('/content/tour_for_tl_loss.png')

In [ ]:
model.save_weights('dis_postagging_final_cdtl.h5')

In [ ]:
acc = hist_final.history['acc']
val_acc = hist_final.history['val_acc']
loss = hist_final.history['loss']
val_loss = hist_final.history['val_loss']
plt.plot(acc)
plt.plot(val_acc)
plt.xlabel("no of epochs")
plt.ylabel("train accuracy and validation accuracy")
plt.legend(["train acc","validation acc"],loc='upper right')
plt.title("accuray vs validation accuracy after transfer learning on dis postagging data ")
plt.savefig("dis_after_tl_acc.png")
plt.show()
files.download("/content/dis_after_tl_acc.png")

In [ ]:
plt.plot(loss)
plt.plot(val_loss)
plt.xlabel("no of epochs")
plt.ylabel("train loss and validation loss")
plt.legend(["train loss","validation loss"],loc='upper right')
plt.title("train loss vs validation loss after transfer learning on dis postagging data ")
plt.savefig("dis_after_tl_loss.png")
plt.show()
files.download('/content/dis_after_tl_loss.png')

In [ ]:
def CrossDomain_base1(word_to_vec_map, word_to_vec_map1, word_to_index,num_of_label):
  input_shape = (52,)
  

  sentence_indices = Input(shape=input_shape,dtype='int32',name='input')
  embedding_layer = pretrained_embedding_layer(word_to_vec_map,word_to_vec_map1 ,word_to_index)
  embeddings = embedding_layer(sentence_indices)

  
  
  mixed_embeddings = embeddings

  print(mixed_embeddings)
  X = Bidirectional(GRU(units=128,return_sequences=True))(mixed_embeddings)

  X = Bidirectional(GRU(units=128,return_sequences=True))(X)
  print(X.shape)
  X = Dropout(rate=0.5)(X)
  print(X.shape)
  X = Bidirectional(GRU(units=128,return_sequences=True))(X)
  print(X.shape)
  X = Dropout(rate=0.5)(X)
  print(X.shape)
 

  X = Dense(units=num_of_label)(X)
  X= Activation('softmax')(X)
  print(X.shape)

  model = Model(inputs=sentence_indices,outputs=X)
  return model

# **Adversarial Learning**
[Tensorflow Keras Neural Structured Learning Framework](https://www.tensorflow.org/neural_structured_learning/tutorials/adversarial_keras_cnn_mnist)

In [ ]:
!pip install --quiet neural_structured_learning


     |████████████████████████████████| 122kB 4.8MB/s 


In [ ]:
import neural_structured_learning as nsl

In [ ]:
class HyperParam(object):
  def __init__(self):
    self.adv_multiplier = 0.2
    self.adv_step_size = 0.2
    self.adv_grade_norm = 'infinity'
HPARAM = HyperParam()

In [ ]:
adv_configs = nsl.configs.make_adv_reg_config(multiplier=HPARAM.adv_multiplier,adv_step_size=HPARAM.adv_step_size,adv_grad_norm=HPARAM.adv_grade_norm)

ADV MODEL FOR ARTICLES AND CONVERSATION

In [ ]:
opt = Adam(lr=0.02, beta_1=0.9, beta_2=0.999, decay=0.007)
base_adv_model = CrossDomainChunk({},{},word_index,81)
adv_model = nsl.keras.AdversarialRegularization(
    base_adv_model,
    label_keys=['label'],
    adv_config=adv_configs
)


52
(?, 16)
(?, 52, 100)
(?, 52, 16)
Tensor("concatenate_1/concat:0", shape=(?, 52, 116), dtype=float32)
(?, 52, 256)
(?, 52, 256)
Tensor("lambda_107/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("lambda_107/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("lambda_107/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("lambda_107/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 1)
(10, 1, 1)
(?, 52, 1)
(?, 52, 256)


In [ ]:

adv_model.compile(optimizer=opt, loss='categorical_crossentropy', metrics=['accuracy']) 

In [ ]:

batch_size=32
train_data_art = tf.data.Dataset.from_tensor_slices(
    {'input':train_padded_word_sequences_articles[:13000],'input1':train_padded_charword_sequences_articles[:13000],'label':all_domains_train_padded_label_sequence_one_hot_articles[:13000]}).batch(batch_size)
val_data_art = tf.data.Dataset.from_tensor_slices(
   {'input':train_padded_word_sequences_articles[13000:],'input1':train_padded_charword_sequences_articles[13000:],'label':all_domains_train_padded_label_sequence_one_hot_articles[13000:]}).batch(batch_size)
val_steps_art =2088/ batch_size
test_data_art=tf.data.Dataset.from_tensor_slices(
   {'input':test_padded_word_sequences_articles,'input1':test_padded_charword_sequences_articles,'label':all_domains_test_padded_label_sequence_one_hot_articles}).batch(batch_size)


In [ ]:

batch_size=32
train_data = tf.data.Dataset.from_tensor_slices(
    {'input':train_padded_word_sequences_conv[:1300],'input1':train_padded_charword_sequences_conv[:1300],'label':all_domains_train_padded_label_sequence_one_hot_conv[:1300]}).batch(batch_size).shuffle(1000)
val_data = tf.data.Dataset.from_tensor_slices(
   {'input':train_padded_word_sequences_conv[1300:],'input1':train_padded_charword_sequences_conv[1300:],'label':all_domains_train_padded_label_sequence_one_hot_conv[1300:]}).batch(batch_size)
val_steps =400/ batch_size
test_data_conv = tf.data.Dataset.from_tensor_slices(
    {'input':test_padded_word_sequences_conv,'input1':test_padded_charword_sequences_conv,'label':all_domains_test_padded_label_sequence_one_hot_conv}).batch(batch_size)




# train_dataset= train_dataset.map(convert_to_tuples)
# train_set_conv= map(convert_to_dictionaries,train_dataset)  

In [ ]:
adv_model.load_weights('/content/adv_mocha_l2l_cd_art_tour_conv_part1.h5')

In [ ]:

es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=10)
adv_model.fit(train_data , validation_data=val_data,validation_steps=val_steps, epochs=40, verbose=1,callbacks=[es])

In [ ]:
adv_model.evaluate(test_data_conv)

In [ ]:
 adv_model.save_weights("adv_mocha_l2l_cd_art_tour_conv_part2.h5")

In [ ]:
adv_model.fit(train_data_tour, validation_data=val_data_tour,
              validation_steps=val_steps_tour, epochs=60, verbose=1,callbacks=[es])

ADV MODEL FOR TOUR AND DIS

In [ ]:
opt = Adam(lr=0.02, beta_1=0.9, beta_2=0.999, decay=0.01)
base_adv_model = CrossDomainChunk({},{},word_index,81)
adv_model = nsl.keras.AdversarialRegularization(
    base_adv_model,
    label_keys=['label'],
    adv_config=adv_configs
)


In [ ]:
adv_model.compile(optimizer=opt, loss='categorical_crossentropy', metrics=['accuracy']) 

In [ ]:

batch_size=32
train_data_dis = tf.data.Dataset.from_tensor_slices(
    {'input':train_padded_word_sequences_dis[:600],'input1':train_padded_charword_sequences_dis[:600],'label':all_domains_train_padded_label_sequence_one_hot_dis[:600]}).batch(batch_size)
val_data_dis = tf.data.Dataset.from_tensor_slices(
{'input':train_padded_word_sequences_dis[600:],'input1':train_padded_charword_sequences_dis[600:],'label':all_domains_train_padded_label_sequence_one_hot_dis[600:]}).batch(batch_size)
val_steps_dis =300/ batch_size
test_data_dis = tf.data.Dataset.from_tensor_slices(
    {'input':test_padded_word_sequences_dis,'input1':test_padded_charword_sequences_dis,'label':all_domains_test_padded_label_sequence_one_hot_dis}).batch(batch_size)



In [ ]:

batch_size=32
train_data_tour = tf.data.Dataset.from_tensor_slices(
    {'input':train_padded_word_sequences_tour[:2000],'input1':train_padded_charword_sequences_tour[:2000],'label':all_domains_train_padded_label_sequence_one_hot_tour[:2000]}).batch(batch_size)
val_data_tour = tf.data.Dataset.from_tensor_slices(
   {'input':train_padded_word_sequences_tour[2000:],'input1':train_padded_charword_sequences_tour[2000:],'label':all_domains_train_padded_label_sequence_one_hot_tour[2000:]}).batch(batch_size)
val_steps_tour =400/ batch_size
test_data_tour = tf.data.Dataset.from_tensor_slices(
    {'input':test_padded_word_sequences_tour,'input1':test_padded_charword_sequences_tour,'label':all_domains_test_padded_label_sequence_one_hot_tour}).batch(batch_size)


# train_dataset= train_dataset.map(convert_to_tuples)
# train_set_conv= map(convert_to_dictionaries,train_dataset)  

In [ ]:
es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=10)

adv_model.fit(train_data_tour, validation_data=val_data_tour,
              validation_steps=val_steps, epochs=40, verbose=1)

In [ ]:
 adv_model.fit(train_data_dis, validation_data=val_data_dis,validation_steps=val_steps_dis, epochs=20, verbose=1)

In [ ]:
adv_model.save_weights('/content/adv_mocha_l2l_cd_art_conv_part1.h5')

In [ ]:
adv_model.evaluate(test_data_dis)

In [ ]:
adv_model.load_weights('/content/adv_mocha_l2l_cd_conv_dis_part1.h5')

In [ ]:
def transfer_weights_adv(layer_num,model_1,model_2):
  
  for i in layer_num:
    model_1.layers[0].layers[-i].set_weights(model_2.layers[0].layers[-i].get_weights())

def repo_adv(test_data,name,adv_model):
  y_pre= adv_model.predict(test_data_dis)

  y_pred=y_pre.argmax(-1)
  prediction =asarray(y_pred)
  print(prediction[0])
  prediction = pd.DataFrame(prediction).to_csv(name)

  classification_report_org(all_domains_padded_label_sequence_dis_final_one_hot.argmax(-1),y_pred,label_all_domain_mix)




def tf_partial_layers_adv(layer_num,file_name,model_s_data,model_t_data,lr_s,lr_t,epochs_s,epochs_t,test_data,name,val_data,val_steps):
  es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=15)

  opt_s = Adam(lr_s, beta_1=0.9, beta_2=0.999, decay=0.01)
  # model_s = CrossDomainChunk({},{},word_index,81)
  base_adv_model = CrossDomainChunk({},{},word_index,81)
  model_s = nsl.keras.AdversarialRegularization(
    base_adv_model,
    label_keys=['label'],
    adv_config=adv_configs
  )

  model_s.compile(optimizer=opt_s, loss='categorical_crossentropy', metrics=['accuracy']) 


  if file_name!="":
    model_s.load_weights(file_name)
  else :   
    model_s.fit(model_s_data, validation_data=val_data_dis,validation_steps=val_steps_dis, epochs=10, verbose=1,callbacks=[es])
    model_s.save_weights('temp.h5')



  
  opt_t = Adam(lr_t, beta_1=0.9, beta_2=0.999, decay=0.01)
  base_model_t = CrossDomainChunk({},{},word_index,81)

  model_t = nsl.keras.AdversarialRegularization(
    base_model_t,
    label_keys=['label'],
    adv_config=adv_configs
  )

  model_t.compile(optimizer=opt_t, loss='categorical_crossentropy', metrics=['accuracy']) 



  transfer_weights_adv(layer_num,model_s,model_t)


  
  model_s.fit(model_t_data, validation_data=val_data,validation_steps=val_steps, epochs=epochs_t, verbose=1,callbacks=[es])
  model_name= name +'.h5'
  model_s.save_weights(model_name)

  csv_name= name +'.csv'
  repo_adv(test_data,csv_name,model_s)



In [ ]:
layer_num=[1,2,3,4]
file_name="/content/drive/My Drive/ADVERSIAL MODELS/layer_to_layer/adv_mocha_l2l_cd_art_tour_conv_part2.h5"
model_s_data=train_data_tour
model_t_data=train_data_dis
epochs_s=50
epochs_t=100
lr_s=0.02
lr_t=0.02
test_data=test_data_dis
name_for_saving="adv_mocha_l2l_cd_art_tour_conv_dis_part1"

In [ ]:
tf_partial_layers_adv(layer_num,file_name,model_s_data,model_t_data,lr_s,lr_t,epochs_s,epochs_t,test_data,name_for_saving,val_data_dis,val_steps_dis)

52
(?, 16)
(?, 52, 100)
(?, 52, 16)
Tensor("concatenate_6/concat:0", shape=(?, 52, 116), dtype=float32)
(?, 52, 256)
(?, 52, 256)
Tensor("lambda_377/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("lambda_377/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("lambda_377/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("lambda_377/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 1)
(10, 1, 1)
(?, 52, 1)
(?, 52, 256)
52
(?, 16)
(?, 52, 100)
(?, 52, 16)
Tensor("concatenate_7/concat:0", shape=(?, 52, 116), dtype=float32)
(?, 52, 256)
(?, 52, 256)
Tensor("lambda_431/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("lambda_431/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("lambda_431/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("lambda_431/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 

(?, 52, 256)
Tensor("AdversarialRegularization_3/model_6/lambda_377/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("AdversarialRegularization_3/model_6/lambda_377/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("AdversarialRegularization_3/model_6/lambda_377/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("AdversarialRegularization_3/model_6/lambda_377/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 1)
(10, 1, 1)
(?, 52, 1)


(?, 52, 256)
Tensor("AdversarialRegularization_3/model_6_1/lambda_377/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("AdversarialRegularization_3/model_6_1/lambda_377/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("AdversarialRegularization_3/model_6_1/lambda_377/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("AdversarialRegularization_3/model_6_1/lambda_377/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 1)
(10, 1, 1)
(?, 52, 1)


Train on 19 steps, validate on 9.375 steps
Epoch 1/100
19/19 [==============================] - 56s 3s/step - loss: 2.8144 - categorical_crossentropy: 2.3451 - categorical_accuracy: 0.4531 - scaled_adversarial_loss: 0.4693 - val_loss: 1.8722 - val_categorical_crossentropy: 1.4627 - val_categorical_accuracy: 0.5699 - val_scaled_adversarial_loss: 0.2925
Epoch 2/100
19/19 [==============================] - 17s 905ms/step - loss: 1.5353 - categorical_crossentropy: 1.2797 - categorical_accuracy: 0.6156 - scaled_adversarial_loss: 0.2556 - val_loss: 1.3775 - val_categorical_crossentropy: 1.0761 - val_categorical_accuracy: 0.6630 - val_scaled_adversarial_loss: 0.2152
Epoch 3/100
19/19 [==============================] - 17s 914ms/step - loss: 1.2438 - categorical_crossentropy: 1.0365 - categorical_accuracy: 0.6747 - scaled_adversarial_loss: 0.2074 - val_loss: 1.1102 - val_categorical_crossentropy: 0.8674 - val_categorical_accuracy: 0.7374 - val_scaled_adversarial_loss: 0.1735
Epoch 4/100
19/19 

In [ ]:
layer_num=[6,7]
file_name="/content/drive/My Drive/ADVERSIAL MODELS/layer_to_layer/adv_mocha_l2l_cd_art_tour_conv_part2.h5"
model_s_data=train_data_tour
model_t_data=train_data_dis
epochs_s=50
epochs_t=100
lr_s=0.01
lr_t=0.01
test_data=test_data_dis
name_for_saving="adv_mocha_l2l_cd_art_tour_conv_dis_part2"

In [ ]:
tf_partial_layers_adv(layer_num,file_name,model_s_data,model_t_data,lr_s,lr_t,epochs_s,epochs_t,test_data_dis,name_for_saving,val_data_dis,val_steps_dis)

52
(?, 16)
(?, 52, 100)
(?, 52, 16)
Tensor("concatenate_4/concat:0", shape=(?, 52, 116), dtype=float32)
(?, 52, 256)
(?, 52, 256)
Tensor("lambda_269/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("lambda_269/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("lambda_269/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("lambda_269/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 1)
(10, 1, 1)
(?, 52, 1)
(?, 52, 256)
52
(?, 16)
(?, 52, 100)
(?, 52, 16)
Tensor("concatenate_5/concat:0", shape=(?, 52, 116), dtype=float32)
(?, 52, 256)
(?, 52, 256)
Tensor("lambda_323/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("lambda_323/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("lambda_323/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("lambda_323/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 

(?, 52, 256)
Tensor("AdversarialRegularization_1/model_4/lambda_269/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("AdversarialRegularization_1/model_4/lambda_269/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("AdversarialRegularization_1/model_4/lambda_269/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("AdversarialRegularization_1/model_4/lambda_269/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 1)
(10, 1, 1)
(?, 52, 1)


(?, 52, 256)
Tensor("AdversarialRegularization_1/model_4_1/lambda_269/Exp:0", shape=(?, 52, 256), dtype=float32)
Tensor("AdversarialRegularization_1/model_4_1/lambda_269/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 52, 256)
Tensor("AdversarialRegularization_1/model_4_1/lambda_269/Maximum:0", shape=(?, 52, 256), dtype=float32)
(?, 61, 256)
(?, 61, 256)
(10, 256, 1)
(?, 52, 1)
(?, 52, 1)
Tensor("AdversarialRegularization_1/model_4_1/lambda_269/truediv:0", shape=(?, 52, 1), dtype=float32)
(?, 61, 1)
(?, 61, 1)
(10, 1, 1)
(?, 52, 1)


Train on 19 steps, validate on 9.375 steps
Epoch 1/100
19/19 [==============================] - 51s 3s/step - loss: 4.1155 - categorical_crossentropy: 3.4235 - categorical_accuracy: 0.5130 - scaled_adversarial_loss: 0.6919 - val_loss: 1.6151 - val_categorical_crossentropy: 1.2618 - val_categorical_accuracy: 0.7097 - val_scaled_adversarial_loss: 0.2524
Epoch 2/100
19/19 [==============================] - 18s 935ms/step - loss: 1.3768 - categorical_crossentropy: 1.1473 - categorical_accuracy: 0.7116 - scaled_adversarial_loss: 0.2295 - val_loss: 0.8797 - val_categorical_crossentropy: 0.6873 - val_categorical_accuracy: 0.8053 - val_scaled_adversarial_loss: 0.1375
Epoch 3/100
19/19 [==============================] - 18s 935ms/step - loss: 0.8702 - categorical_crossentropy: 0.7243 - categorical_accuracy: 0.7965 - scaled_adversarial_loss: 0.1459 - val_loss: 0.6617 - val_categorical_crossentropy: 0.5169 - val_categorical_accuracy: 0.8534 - val_scaled_adversarial_loss: 0.1034
Epoch 4/100
19/19 

Download area



In [ ]:
from google.colab import files
files.download('adv_mocha_l2l_cd_art_dis_part2.h5')
files.download('prediction_adv_art_dis_l2l_part2.csv')

# ***REPORTS***

In [ ]:

import numpy as np
import pandas as pd

from numpy import asarray
from numpy import savetxt
# define data


In [ ]:
import numpy 
from collections import Counter
import pandas as pd

def classification_report_org(y_true, y_pred, labels):
	'''Similar to the one in sklearn.metrics,
	reports per classs recall, precision and F1 score'''
	# print(y_pred)
	# print(y_true)
	y_true = numpy.asarray(y_true).ravel()
	y_pred = numpy.asarray(y_pred).ravel()

	corrects = Counter(yt for yt, yp in zip(y_true, y_pred) if yt == yp)
	y_true_counts = Counter(y_true)
	y_pred_counts = Counter(y_pred)
	report = ((lab,  # label
			   corrects[i] / max(1, y_true_counts[i]),  # recall
			   corrects[i] / max(1, y_pred_counts[i]),  # precision
			   y_true_counts[i]  # support
			   ) for i, lab in enumerate(labels))
	report = [(l, r, p, 2 * r * p / max(1e-9, r + p), s) for l, r, p, s in report]

	print('{:<15}{:>10}{:>10}{:>10}{:>10}\n'.format('',
													'recall',
													'precision',
													'f1-score',
													'support'))
	formatter = '{:<15}{:>10.4f}{:>10.4f}{:>10.4f}{:>10d}'.format
	for r in report:
		print(formatter(*r))
	print('')
	report2 = list(zip(*[(r * s, p * s, f1 * s) for l, r, p, f1, s in report]))
	N = len(y_true)
	print(formatter('avg / total',
					sum(report2[0]) / N,
					sum(report2[1]) / N,
					sum(report2[2]) / N, N) + '\n')
	actual = Counter(y_true)
	del actual[-1]
	accuracy = sum(corrects.values()) / sum(actual.values())
	print('Accuracy:', accuracy)


def classification_report_1(y_true, y_pred, labels):
    '''Similar to the one in sklearn.metrics,
    reports per classs recall, precision and F1 score'''
    # print(y_pred)
    # print(y_true)
    y_true = numpy.asarray(y_true).ravel()
    y_pred = numpy.asarray(y_pred).ravel()
    corrects = Counter(yt for yt, yp in zip(y_true, y_pred) if yt == yp)
    incorrects = Counter(yt for yt, yp in zip(y_true, y_pred) if yt != yp )
  
  
    y_true_counts = Counter(y_true)
    y_pred_counts = Counter(y_pred)
    report = ((lab,  # label
               corrects[i] / max(1, y_true_counts[i]),  # recall
               corrects[i] / max(1, y_pred_counts[i]),  # precision
               y_true_counts[i],corrects[i],incorrects[i]) for i, lab in enumerate(labels))
    report_analysis=[(l,cor,incor,total) for l, rec, pre, total, cor, incor in report]
    report = [(l, r, p, 2 * r * p / max(1e-9, r + p), s) for l, r, p, s in report]

    # print('{:<15}{:>10}{:>10}{:>10}{:>10}\n'.format('',
    #                                                 'recall',
    #                                                 'precision',
    #                                                 'f1-score',
    #                                                 'support'))
    # formatter = '{:<15}{:>10.2f}{:>10.2f}{:>10.2f}{:>10d}'.format
    # for r in report:
    #     print(formatter(*r))
    # print('')
    # report2 = list(zip(*[(r * s, p * s, f1 * s) for l, r, p, f1, s in report]))
    # N = len(y_true)
    # print(formatter('avg / total',
    #                 sum(report2[0]) / N,
    #                 sum(report2[1]) / N,
    #                 sum(report2[2]) / N, N) + '\n')
    # actual = Counter(y_true)
    # del actual[-1]
    # accuracy = sum(corrects.values()) / sum(actual.values())
    # print('Accuracy:', accuracy)

    
    print('label  true_pos  false_pos   Total')
    total=[]
    label=[]
    correct=[]
    incorrect=[]
    error=[]
    for lab,cor,incor,tot in report_analysis:
      # print(lab,"    ",cor,"    ",incor,"     ",tot,"         ",((tot-cor)/tot ))
      label.append(lab)
      correct.append(cor)
      incorrect.append(incor)
      total.append(tot)
      if tot!=0:
        error.append(((tot-cor)/tot ))
      else :
        error.append(0)

    return label,correct,total,error      



Articles Advers + dis

In [ ]:
adv_model.load_weights('/content/adv_mocha_l2l_cd_art_tour_conv_dis_part1.h5')


adv_model.evaluate(test_data_dis)
y_pre= adv_model.predict(test_data_dis)

y_pred=y_pre.argmax(-1)
prediction =asarray(y_pred)
print(prediction[0])
prediction = pd.DataFrame(prediction).to_csv('prediction_adv_art_tour_conv_part1.csv')

classification_report_org(all_domains_test_padded_label_sequence_one_hot_dis.argmax(-1),y_pred,label_all_domain_mix)


19/19 [==============================] - 12s 611ms/step - loss: 0.3980 - categorical_crossentropy: 0.3317 - categorical_accuracy: 0.9468 - scaled_adversarial_loss: 0.0663
[14  1  2  1  6  1  6  1  2  3  2  2  4  7  7  5  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0]
                   recall precision  f1-score   support

n_nn               0.9997    0.9988    0.9992     16784
psp                0.9429    0.8500    0.8940      3360
n_nnp              0.9764    0.9748    0.9756      2374
v_vm               0.5455    0.8712    0.6709       583
rd_punc            0.8680    0.9066    0.8869      1364
jj                 0.9852    0.9683    0.9767      1148
v_vaux             0.8440    0.7564    0.7978      1122
qt_qtc             0.9367    0.9534    0.9450      1201
cc_ccd             0.7888    0.7704    0.7795       251
rp_rpd             0.9698    0.8552    0.9089       463
pr_prp             0.6549    0.8810    0.7513       

# ***Adversal articles + Tour***

In [ ]:
# adv_model.load_weights('/content/drive/My Drive/ADVERSIAL MODELS/adv_cd_articles_tour.h5')


adv_model.evaluate(test_data_tour)
y_pre= adv_model.predict(test_data_tour)

y_pred=y_pre.argmax(-1)
prediction =asarray(y_pred)
print(prediction[0])
prediction = pd.DataFrame(prediction).to_csv('prediction_adv_art_tour_l2l_part2.csv')

classification_report_org(all_domains_test_padded_label_sequence_one_hot_tour.argmax(-1),y_pred,label_all_domain_mix)


# ***adver Tour + dis***

In [ ]:
adv_model.load_weights('/content/adv_mocha_l2l_cd_art_tour_conv_part2.h5')


adv_model.evaluate(test_data_conv)
y_pre= adv_model.predict(test_data_conv)

y_pred=y_pre.argmax(-1)
prediction =asarray(y_pred)
print(prediction[0])
prediction = pd.DataFrame(prediction).to_csv('prediction_adv_art_tour_conv_part2.csv')

classification_report_org(all_domains_test_padded_label_sequence_one_hot_conv.argmax(-1),y_pred,label_all_domain_mix)


# ***Adver Tour + conv***

In [ ]:
adv_model.load_weights('/content/adv_mocha_l2l_cd_art_conv_part2.h5')

adv_model.evaluate(test_data_conv)

y_pre= adv_model.predict(test_data_conv)

y_pred=y_pre.argmax(-1)

prediction =asarray(y_pred)

print(prediction[0])

prediction = pd.DataFrame(prediction).to_csv('prediction_adv_conv_part2_l2l.csv')

classification_report_org(all_domains_test_padded_label_sequence_one_hot_conv.argmax(-1),y_pred,label_all_domain_mix)


# ***Adv tour + dis***

In [ ]:
adv_model.load_weights('/content/drive/My Drive/ADVERSIAL MODELS/layer_to_layer/adv_mocha_l2l_cd_art_dis_part2.h5')


adv_model.evaluate(test_data_dis)
y_pre= adv_model.predict(test_data_dis)

y_pred=y_pre.argmax(-1)
prediction =asarray(y_pred)
print(prediction[0])
prediction = pd.DataFrame(prediction).to_csv('prediction_adv_art_dis_l2l_part2.csv')

classification_report_org(all_domains_test_padded_label_sequence_one_hot_dis.argmax(-1),y_pred,label_all_domain_mix)


# ***Art + tour + dis***

In [ ]:
adv_model.load_weights('/content/drive/My Drive/ADVERSIAL MODELS/ADV_TOUR_dis.h5')


adv_model.evaluate(test_data_dis)
y_pre= adv_model.predict(test_data_dis)

y_pred=y_pre.argmax(-1)
prediction =asarray(y_pred)
print(prediction[0])
prediction = pd.DataFrame(prediction).to_csv('prediction_adv_tour_dis.csv')

classification_report_org(all_domains_test_padded_label_sequence_one_hot_dis.argmax(-1),y_pred,label_all_domain_mix)
